In [21]:
%load_ext autoreload
%autoreload 2
import os
import holoviews as hv
import numpy as np
import pandas as pd
import LocationTracking_Functions as lt

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [22]:
video_dict = {
    'dpath'        : r'Z:\Ali O\yarm_miniscope_recording\m25lr\m25lr_6\2023_01_12_r2_good_dlc\10_15_08\My_WebCam',
    'file'         : '0.avi',
    'start'        : 0,
    'end'          : None,
    'region_names' : ['spout1','main1','inter','spout2','main2','spout3','main3'],
    'dsmpl'        : 1,
    'stretch'      : dict(width=1, height=1)
}

In [23]:
%%output size = 50

img_crp, video_dict = lt.LoadAndCrop(video_dict, cropmethod='Box')
img_crp

file: Z:\Ali O\yarm_miniscope_recording\m25lr\m25lr_6\2023_01_12_r2_good_dlc\10_15_08\My_WebCam\0.avi
total frames: 72164
nominal fps: 60.0
dimensions (h x w): 480,640


:Overlay
   .Image.I    :Image   [x,y]   (z)
   .Polygons.I :Polygons   [x,y]

In [24]:
%%output size = 100

#video_dict['reference'], img_ref = lt.Reference(video_dict, num_frames=50, frames=np.arange(30,80,1)) 
video_dict['reference'], img_ref = lt.Reference(video_dict, num_frames=50, frames=None) 
img_ref

:Image   [x,y]   (z)

# 6. Use Interactive Plot to Define Regions of Interest.  

After running cell below, draw regions of interest on presented image in the order you provided them (in Cell 2).  To start drawing a region, double click on image.  Single click to add a vertex.  Double click to close polygon.  If you mess up it's easiest to re-run cell.

***Note*** that there are no problems if regions overlap.

In [26]:
%%output size = 100 

img_roi, video_dict['roi_stream'] = lt.ROI_plot(video_dict)
img_roi

:DynamicMap   []
   :Overlay
      .Image.I    :Image   [x,y]   (z)
      .Polygons.I :Polygons   [x,y]
      .Labels.I   :Labels   [x,y]   (Label)

In [27]:
tracking_params = {
    'loc_thresh'    : 99.5, 
    'use_window'    : True, 
    'window_size'   : 100, 
    'window_weight' : .9, 
    'method'        : 'abs',
    'rmv_wire'      : True, 
    'wire_krn'      : 5
}

In [28]:
location = lt.tempTrackLocation(video_dict, tracking_params)   
location.to_csv(os.path.splitext(video_dict['fpath'])[0] + '_tempLocationOutput.csv', index=False)
location.head()

total frames processed: 72164



File  Location_Thresh Use_Window  Window_Weight  Window_Size  Start_Frame  \
2  0.avi             99.5       True            0.9        100.0          0.0   
3  0.avi             99.5       True            0.9        100.0          0.0   
4  0.avi             99.5       True            0.9        100.0          0.0   
5  0.avi             99.5       True            0.9        100.0          0.0   
6  0.avi             99.5       True            0.9        100.0          0.0   

   Frame                   X                   Y         Distance_px  
2      0  210.45578002929688   443.8609313964844   443.8609313964844  
3      1   210.7554931640625  443.79302978515625  443.79302978515625  
4      2  211.53465270996094  442.07086181640625  442.07086181640625  
5      3   212.3975372314453  443.81414794921875  443.81414794921875  
6      4  213.38710021972656   444.1863098144531   444.1863098144531

In [29]:
location = lt.TrackLocation(video_dict, tracking_params)   
location.to_csv(os.path.splitext(video_dict['fpath'])[0] + 'fixed_LocationOutput.csv', index=False)
location.head()

Defining transitions...


File  Location_Thresh  Use_Window  Window_Weight  Window_Size  \
0  0.avi             99.5        True            0.9        100.0   
1  0.avi             99.5        True            0.9        100.0   
2  0.avi             99.5        True            0.9        100.0   
3  0.avi             99.5        True            0.9        100.0   
4  0.avi             99.5        True            0.9        100.0   

   Start_Frame  Frame           X           Y  Distance_px  spout1  main1  \
0          0.0      0  210.455780  443.860931   443.860931    True  False   
1          0.0      1  210.755493  443.793030   443.793030    True  False   
2          0.0      2  211.534653  442.070862   442.070862    True  False   
3          0.0      3  212.397537  443.814148   443.814148    True  False   
4          0.0      4  213.387100  444.186310   444.186310    True  False   

   inter  spout2  main2  spout3  main3  \
0  False   False  False   False  False   
1  False   False  False   False  False   
2  False   False  False   False  False   
3  False   False  False   False  False   
4  False   False  False   False  False   

                                     ROI_coordinates ROI_location  \
0  {'xs': [[180.35322131849315, 281.8013622186888...       spout1   
1  {'xs': [[180.35322131849315, 281.8013622186888...       spout1   
2  {'xs': [[180.35322131849315, 281.8013622186888...       spout1   
3  {'xs': [[180.35322131849315, 281.8013622186888...       spout1   
4  {'xs': [[180.35322131849315, 281.8013622186888...       spout1   

   ROI_transition  
0           False  
1           False  
2           False  
3           False  
4           False

In [30]:
#reads csv from specified path
df = pd.read_csv(video_dict['dpath']+'\\0fixed_LocationOutput.csv')
#print(df)
#filters by column headers
filter1 = df.loc[:, ["Frame", "ROI_location", "ROI_transition"]]

#creates dataframe to edit values from previous filter
dataframe = pd.DataFrame(filter1, columns=['Frame', "ROI_location", "ROI_transition"]) 
#print("Filter 1 :\n", dataframe)

# selecting rows based on condition, .isin passes list like types
options = ['spout1', 'spout2','spout3','main1','main2','main3','inter']     
rslt_df = dataframe.loc[dataframe['ROI_location'].isin(options)]
#print('\n Filtered locations :\n', rslt_df)

  
# selecting rows based on condition 
rslt_df2 = rslt_df[(rslt_df['ROI_transition']==True)]
#print('\n Filtered locations & True :\n',rslt_df2)

rslt_df2['ROI_location'] = rslt_df2['ROI_location'].replace({'spout1':'spout', 'spout2':'spout','spout3':'spout','main1':'main','main2':'main','main3':'main'})

#rename main1,main2,main3 to main & rename spout1,spout2,spout3 to spout
#rslt_df2.to_csv(os.path.splitext(video_dict['fpath'])[0] + 'locseq.csv', index=False)

rslt_df2.to_csv(video_dict['dpath'] + '\\loc_seq.csv', index=False)
